In [24]:
import re
import logging
import requests
from bs4 import BeautifulSoup

HEADERS = {
    "User-Agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/112.0.0.0 YaBrowser/23.5.1.762 Yowser/2.5 Safari/537.36",
    "Content-Type": "application/json",
}

In [73]:
import json

with open("../naked_science_articles_snippets.json", "r") as f:
    data = json.load(f)

len(data)

4020

In [1]:
import json

with open("../naked_science_corpus.json", "r") as f:
    data = json.load(f)

data

[{'article_link': 'https://naked-science.ru/article/biology/ihtiologishumom-reaktivno',
  'article_title': 'Ихтиологи узнали, как сантиметровая рыбка издает звуки, сравнимые с шумом реактивного двигателя',
  'article_category': 'Биология',
  'text': 'Danionella cerebrum — крошечная прозрачная рыбка семейства карповых, вид которой открыли всего пару лет назад. До этого полагали, что Danionella cerebrum относится к другому виду — Danionella translucida из-за внешнего сходства и похожего ареала. И тот, и другой вид водится в Мьянме, в мелких ручейках и мутных водоемах. Внешне Danionella cerebrum ничем не примечательна, но это обманчиво. Дело в том, что данионелла способна издавать звуки мощностью более 140 децибел на расстоянии длины своего тела — от 10 до 12 миллиметров. Это сравнимо с шумом взлетающего самолета, который воспринимает человек, стоящий на расстоянии ста метров от него. Для столь миниатюрных существ это явление весьма нетипично. Ученые из Центра нейробиологии имени Эйнштейн

In [1]:
import json

with open("naked_science_articles_links.json", "w") as f:
    json.dump(["a", "b", "c"], f)

In [25]:
from parser_naked_science import (
    clean_string,
    parse_articles_snippets,
    parse_article_content,
)

logging.basicConfig(
    level=logging.INFO,
    filename="habr_parser.log",
    filemode="w",
    format="%(asctime)s %(levelname)-8s [%(filename)s:%(lineno)d] %(message)s",
)
logger = logging.getLogger()

PAGES_LIMIT = 2
corpus = []
words_count = 0
domain = "https://naked-science.ru/"
corpus = parse_articles_snippets(domain, logger, pages_limit=PAGES_LIMIT)

[INFO] Parsed 20 links, page 1
[INFO] Parsed 40 links, page 2
[INFO] Parsed 60 links, page 3
[INFO] Reached pages limit [2], exiting...


In [30]:
import pickle

with open("filename.pickle", "wb") as handle:
    pickle.dump(corpus, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open("naked_science_articles_snippets.json", "w") as f:
    json.dump(corpus, f)

In [32]:
corpus

[{'article_link': 'https://naked-science.ru/article/column/v-pniekspluatatsii-plastm',
  'article_title': 'В ПНИПУ разработали модель для полного контроля производства и эксплуатации пластмассовых изделий',
  'article_category': 'ПНИПУ'},
 {'article_link': 'https://naked-science.ru/article/column/v-tyueleniya-gazov-i-zhid',
  'article_title': 'В ТюмГУ представили математическую модель разделения газов и жидкостей',
  'article_category': 'ТюмГУ'},
 {'article_link': 'https://naked-science.ru/article/anthropology/teoriyu-pifagora-ob-unive',
  'article_title': 'Теорию Пифагора об универсальной музыкальной гармонии опровергли',
  'article_category': 'Антропология'},
 {'article_link': 'https://naked-science.ru/article/astronomy/largest-galaxy-cluster',
  'article_title': 'Найден «зародыш» крупнейшего скопления галактик во Вселенной',
  'article_category': 'Астрономия'},
 {'article_link': 'https://naked-science.ru/article/astronomy/astronomy-obnaruzhili-sam',
  'article_title': 'Астрономы обн

In [28]:
for k, v in corpus[0].items():
    print(type(k), type(v))

<class 'str'> <class 'str'>
<class 'str'> <class 'str'>
<class 'str'> <class 'str'>


In [2]:
def clean_string(input_string):
    cleaned_string = (
        input_string.replace("\n\n\r\n", " ")
        .replace("\r\n", " ")
        .replace("\n\n", " ")
        .replace("\n", " ")
        .replace("\n\n\n", " ")
        .replace("\n\r\n", " ")
        .replace("\r\n\r\n", " ")
        .replace("\n\n\n\n", " ")
    )
    cleaned_string = " ".join(cleaned_string.split())

    return cleaned_string

Парсинг ссылок на статьи

In [51]:
response = requests.get("https://naked-science.ru/article/page/174/", headers=HEADERS)
bs = BeautifulSoup(response.text, "html.parser")

news_tags = bs.find_all("div", attrs={"class": "news-item grid"})
for tag in news_tags:
    article_link = tag.find("div", attrs={"class": "news-item-title"}).find("a")["href"]
    article_title = tag.find("a", class_="animate-custom").contents[0].get_text()
    article_title = clean_string(article_title)

    category_tag = tag.find("div", attrs={"class": "terms-item terms-item--cat"})
    if not category_tag:
        category_tag = tag.find("div", attrs={"class": "terms-item terms-item--avtor"})
    if category_tag:
        article_category = category_tag.find("a").get_text()
        article_category = clean_string(article_category)

    print(type(article_title), type(article_category), type(article_link))
    print(article_title, article_category, article_link)

<class 'str'> <class 'str'> <class 'str'>
В ТюмГУ изучили историю одного предлога ТюмГУ https://naked-science.ru/article/column/v-tyumgu-izuchili-istoriyu
<class 'str'> <class 'str'> <class 'str'>
Под марсианской равниной обнаружили поток расплавленной магмы Астрономия https://naked-science.ru/article/astronomy/na-marse-obnaruzhili-potok-rasplavlennoj-magmy
<class 'str'> <class 'str'> <class 'str'>
Ученые выяснили, что позднеантичный ледниковый период не был глобальным УрФУ https://naked-science.ru/article/column/uchenye-vyyasnili-chto-pozdneantichnyj
<class 'str'> <class 'str'> <class 'str'>
Новые системы оповещения об опасных сближениях спутников вместо решения проблем создадут свои Космонавтика https://naked-science.ru/article/cosmonautics/ssa-inevitable-problems
<class 'str'> <class 'str'> <class 'str'>
Для поисков темной материи предложили отправить к Солнцу атомные часы Астрономия https://naked-science.ru/article/astronomy/otpravit-k-solntsu-atomnye-chasy
<class 'str'> <class 'st

In [49]:
tag = news_tags[12]
article_link = tag.find("div", attrs={"class": "news-item-title"}).find("a")["href"]
article_title = tag.find("a", class_="animate-custom").contents[0].get_text()
# article_title = clean_string(article_title)

# category_tag = tag.find("div", attrs={"class": "terms-item terms-item--cat"})
# if not category_tag:
#     category_tag = tag.find("div", attrs={"class": "terms-item terms-item--avtor"})
# if category_tag:
#     article_category = category_tag.find("a").get_text()
#     article_category = clean_string(article_category)

# print(type(article_title), type(article_category), type(article_link))

In [47]:
tag.find("a", class_="animate-custom").contents[0].get_text()

'Илон Маск доказал неправоту Билла Гейтса: электрофура Semi «победила» законы физики'

In [17]:
tags[0].find("a", class_="animate-custom").contents[0]

'Найден «зародыш» крупнейшего скопления галактик во Вселенной '

Парсинг контента странцы

In [23]:
import json

with open("naked_science_corpus.json", "r") as f:
    data = json.load(f)

data

[{'article_url': 'https://naked-science.ru/article/astronomy/astronomy-obnaruzhili-sam',
  'category': 'Астрономия',
  'title': 'Астрономы обнаружили самый мощный источник космических лучей Млечного Пути',
  'text': 'Космическими лучами называют заряженные субатомные частицы, такие как протоны или атомные ядра, которые проносятся в пространстве со скоростью близкой к скорости света. Лучи, проходящие через нашу галактику, достигают энергий по меньшей мере в несколько петаэлектронвольт (10 в 15 степени электронвольт), но определить местонахождение их источников заведомо трудная задача. Сложность заключается в том, что космические лучи отражаются от магнитных полей, когда проносятся в космосе, а значит, траектории их полета извилисты. Это и мешает определить место их происхождения. Чтобы обойти проблему, исследователи измеряют фотоны гамма-излучения, образующиеся при взаимодействии космических лучей с межзвездным газом. Гамма-лучи несут 10 процентов энергии космических лучей и распростран

In [10]:
page_url = "https://naked-science.ru/article/column/v-permsozdat-tochnuyu-kop"
response = requests.get(page_url, headers=HEADERS)
bs = BeautifulSoup(response.text, "html.parser")

raw_title = bs.find("div", attrs={"class": "post-title"}).find("h1").get_text()
title = clean_string(raw_title)

category_tag = bs.find("div", attrs={"class": "terms-wrapp"}).find(
    "div", attrs={"class": "terms-item terms-item--cat"}
)
if not category_tag:
    category_tag = bs.find("div", attrs={"class": "terms-wrapp"}).find(
        "div", attrs={"class": "terms-item terms-item--avtor"}
    )
if category_tag:
    raw_category = category_tag.find("a").get_text()
    category = clean_string(raw_category)

article_paragraphs = (
    bs.find("div", attrs={"class": "content"})
    .find("div", attrs={"class": "body"})
    .find_all(["p", "h1", "h2", "h3", "h4", "h5"])
)
article_text = ""
for paragraph in article_paragraphs:
    if paragraph.name in ["h1", "h2", "h3", "h4", "h5"]:
        article_text += clean_string(paragraph.get_text()) + ". "
    else:
        article_text += clean_string(paragraph.get_text()) + " "
article_text = clean_string(article_text)

text = "\n".join([clean_string(p.text) for p in article_paragraphs])
print(title, category, "\n-----\n", text)

# print(f"Title: {title}\nCategory: {category}")

В Пермском Политехе рассказали, можно ли создать точную копию себя ПНИПУ 
-----
 Клонирование — процесс создания генетически идентичной копии клетки, гена или организма. Чаще всего этот термин используют для обозначения искусственных процессов, реже — естественных. Здесь важно понимать, что создать можно именно генетическую копию, а не точно такой же объект. Вся информация о строении организма, его функционировании заложена в структуре ДНК, состоящей из генов, которые отвечают за тот или иной признак. Проявленность конкретного признака зависит не только от наличия гена, но и того, как он реализован (его экспрессии). Это определяется условиями, в которых организм развивается. Для клонированного организма невозможно воссоздать условия, полностью совпадающие с теми, в которых вырос оригинал. Поэтому нельзя получить точную копию, несмотря на одинаковый набор генетической информации.
«Из-за этого хозяева клонированных питомцев могут остаться разочарованными результатом. Кроме того, из-за му

Парсинг ссылок на хабы

In [ ]:
bs = BeautifulSoup(
    requests.get("https://habr.com/ru/hubs/page1/").text,
    "html.parser",
)
tags = bs.find_all("a", attrs={"class": "tm-hub__title"})
links = ["https://habr.com" + l["href"] for l in tags]
print(links)

Пустая страница

In [ ]:
beau = BeautifulSoup(
    requests.get("https://habr.com/ru/hubs/page11/").text,
    "html.parser",
)
not_found_page = beau.find_all("h1", attrs={"class": "tm-error-message__title"})
if not_found_page:
    print(not_found_page)
else:
    print("content")

Парсинг статей с одного хаба

In [ ]:
page_num = 1
beau = BeautifulSoup(
    requests.get(
        "https://habr.com/ru/hubs/kohanaphp/" + "articles/" + f"page{page_num}/"
    ).text,
    "html.parser",
)
not_found_page = beau.find_all("h1", attrs={"class": "tm-error-message__title"})
if not_found_page:
    print(not_found_page)
else:
    tags = beau.find_all("a", attrs={"class": "tm-title__link"})
    links = ["https://habr.com" + l["href"] for l in tags]
    print(links)

Парсинг статей с версией 1

In [ ]:
url = "https://habr.com/ru/companies/kodicms/articles/248937/"
# url = "https://habr.com/ru/articles/796047/"
url = "https://habr.com/ru/post/545634/"

response = requests.get(url)
bs = BeautifulSoup(response.text, "html.parser")

tags = bs.find_all(
    "div",
    attrs={
        "class": "article-formatted-body article-formatted-body article-formatted-body_version-1"
    },
)
article_title = bs.h1.text
article_text = clean_string(tags[0].get_text().strip())
print(article_title)
print(article_text)

Парсинг статей с версией 2

In [ ]:
# url = "https://habr.com/ru/companies/kodicms/articles/248937/"
url = "https://habr.com/ru/articles/796047/"
# url = "https://habr.com/ru/post/545634/"

response = requests.get(url)
bs = BeautifulSoup(response.text, "html.parser")

tags = bs.find_all(
    "div",
    attrs={
        "class": "article-formatted-body article-formatted-body article-formatted-body_version-2"
    },
)
article_title = bs.h1.text
article_paragraphs = tags[0].find_all(["p", "h1", "h2", "h3", "h4", "h5"])
article_text = ""
for paragraph in article_paragraphs:
    if paragraph.name in ["h1", "h2", "h3", "h4", "h5"]:
        article_text += paragraph.get_text() + ". "
    else:
        article_text += paragraph.get_text() + " "

article_text = clean_string(article_text)
print(article_title)
print(article_text)

In [ ]:
# url = "https://habr.com/ru/companies/kodicms/articles/248937/"
# url = "https://habr.com/ru/articles/796047/"
url = "https://habr.com/ru/post/545634/"

response = requests.get(url)
bs = BeautifulSoup(response.text, "html.parser")

tags = bs.find_all(
    "div",
    attrs={
        "class": "article-formatted-body article-formatted-body article-formatted-body_version-2"
    },
)
tags

Общий скрипт

In [ ]:
def parse_hub_links(logger):
    hubs_links = []
    page_num = 1
    while True:
        url = f"https://habr.com/ru/hubs/page{page_num}/"
        response = requests.get(url)
        status_code = response.status_code
        if status_code != 200:
            print(
                f"[WARNING] Error fetching page {url}! Status code: {response.status_code}"
            )
            logger.warning(
                f"Error fetching page {url}! Status code: {response.status_code}"
            )
            break
        else:
            bs = BeautifulSoup(
                response.text,
                "html.parser",
            )

            not_found_page = bs.find_all(
                "h1", attrs={"class": "tm-error-message__title"}
            )
            tags = bs.find_all("a", attrs={"class": "tm-hub__title"})

            if not_found_page or not tags:
                print(f"[WARNING] Page {url} is empty or not found, exiting...")
                logger.warning(f"Page {url} is empty or not found, exiting...")
                break

            links = ["https://habr.com" + l["href"] for l in tags]
            hubs_links.extend(links)
            page_num += 1

            print(f"[INFO] Parsed {len(hubs_links)} links")
            logger.info(f"Parsed {len(hubs_links)} links")

    return hubs_links


def parse_hub_title(hub_url, logger):
    response = requests.get(hub_url)
    bs = BeautifulSoup(response.text, "html.parser")
    hub_title = bs.h1.text.strip()
    hub_title = hub_title.replace("  *", "").strip()
    return hub_title

In [ ]:
def parse_hub_articles(hub_link: str, logger):
    articles_links = []
    page_num = 1
    while True:
        url = f"{hub_link}articles/page{page_num}/"
        response = requests.get(url)
        status_code = response.status_code
        if status_code != 200:
            print(
                f"[WARNING] Error fetching page {url}! Status code: {response.status_code}"
            )
            logger.warning(
                f"Error fetching page {url}! Status code: {response.status_code}"
            )
            break
        else:
            bs = BeautifulSoup(
                response.text,
                "html.parser",
            )
            not_found_page = bs.find_all(
                "h1", attrs={"class": "tm-error-message__title"}
            )
            tags = bs.find_all("a", attrs={"class": "tm-title__link"})

            if not_found_page or not tags:
                print(f"[WARNING] Page {url} is empty or not found, exiting...")
                logger.warning(f"Page {url} is empty or not found, exiting...")
                break

            links = ["https://habr.com" + l["href"] for l in tags]
            articles_links.extend(links)
            page_num += 1

            print(f"[INFO] Parsed {len(articles_links)} links")
            logger.info(f"Parsed {len(articles_links)} links")

    return articles_links

In [ ]:
def get_content_version(bs: BeautifulSoup) -> str:
    tags_v1 = bs.find_all(
        "div",
        attrs={
            "class": "article-formatted-body article-formatted-body article-formatted-body_version-1"
        },
    )
    tags_v2 = bs.find_all(
        "div",
        attrs={
            "class": "article-formatted-body article-formatted-body article-formatted-body_version-2"
        },
    )
    if tags_v1:
        return "1", tags_v1
    if tags_v2:
        return "2", tags_v2
    return None, None


def parse_article_content(url, logger):
    response = requests.get(url)
    status_code = response.status_code
    if status_code != 200:
        print(
            f"[ERROR] Error fetching page content {url}! Status code: {response.status_code}"
        )
        logger.error(
            f"Error fetching page content {url}! Status code: {response.status_code}"
        )
        return None

    bs = BeautifulSoup(response.text, "html.parser")
    content_version, tags = get_content_version(bs)
    if content_version == "1":
        article_text = tags[0].get_text().strip()
    elif content_version == "2":
        article_paragraphs = tags[0].find_all(["p", "h1", "h2", "h3", "h4", "h5"])
        article_text = ""
        for paragraph in article_paragraphs:
            if paragraph.name in ["h1", "h2", "h3", "h4", "h5"]:
                article_text += paragraph.get_text() + ". "
            else:
                article_text += paragraph.get_text() + " "
    else:
        print(f"[ERROR] Undefined conent version for {url}!")
        logger.error(f"Undefined conent version for {url}!")
        return None

    article_title = bs.h1.text
    article_text = clean_string(article_text)

    return article_title, article_text

In [ ]:
logging.basicConfig(
    level=logging.INFO,
    filename="habr_parser.log",
    filemode="w",
    format="%(asctime)s %(levelname)-8s [%(filename)s:%(lineno)d] %(message)s",
)
logger = logging.getLogger()

corpus = []
hubs_links = parse_hub_links(logger)

for hub_url in hubs_links:
    hub_name = parse_hub_title(hub_url, logger)
    articles_links = parse_hub_articles(hub_url, logger)

    for article_url in articles_links:
        article_title, article_text = None, None
        article_content = parse_article_content(article_url, logger)
        if article_content:
            article_title, article_text = article_content
        else:
            print(f"[ERROR] No content found for article: {article_url}")
            logger.error(f"No content found for article: {article_url}")
        corpus.append(
            {
                "hub_url": hub_url,
                "article_url": article_url,
                "hub_name": hub_name,
                "title": article_title,
                "text": article_text,
            }
        )
        print(f"[INFO] Parsed {len(corpus)} articles so far")
        logger.info(f"Parsed {len(corpus)} articles so far")

In [ ]:
corpus = []
corpus.append(
    {
        "hub_url": "hub_url",
        "article_url": "article_url",
        "hub_name": "hub_name",
        "title": "article_title",
        "text": "article_text",
    }
)

In [ ]:
import json

with open("corpus.json", "w") as f:
    json.dump(corpus, f)

In [ ]:
data = None
with open("corpus.json", "r") as f:
    data = json.load(f)

In [ ]:
data